In [ ]:
!pip install plotly

In [ ]:
import sys
print(sys.version)
import numpy as np
import matplotlib.pyplot as plt
import operator
import plotly as plotly
import plotly.graph_objects as go
from mined_metric.jupyter.utils.data_access_util import get_experiment_data, chum_summary_stats

In [ ]:
class ScoresLabels:
    def __init__(self, score, label):
        self.score = score
        self.label = label
        
class PrecisionRecallPoint:
    def __init__(self, precision, recall, score, num_results):
        self.precision = precision
        self.recall = recall
        self.score = score
        self.num_results = num_results
    
def calculatePRPoints(samples):
    scores = []
    labels = []
    for sample in samples:
        if 'classification_result' in sample:
            scores.append(sample['classification_result']['score'])
            labels.append(sample['classification_result']['label'])
    scores_labels_list = []
    npos = 0
    for idx, val in enumerate(scores):
        scores_labels_list.append(ScoresLabels(scores[idx], labels[idx]))
        if labels[idx]:
            npos += 1
    
    if npos == 0:
        return []
    
    scores_labels_list.sort(key=operator.attrgetter('score'), reverse=True)
    
    tp = 0
    fp = 0
    pr_points = []
    for score_label in scores_labels_list:
        if score_label.label:
            tp += 1
        else:
            fp += 1
        if len(pr_points) == 0 or score_label.score != pr_points[-1].score:
            pr_points.append(PrecisionRecallPoint(tp / float(tp + fp), tp / float(npos), score_label.score, tp + fp))
            
    return pr_points

def histogram(hist, x_input, bins_input):
    if len(x_input) == 0:
        return hist
    x_ind = 0
    bin_ind = 0
    while x_ind < len(x_input) and bin_ind < len(bins_input):
        if x_input[x_ind] < bins_input[0]:
            x_ind += 1
        elif x_input[x_ind] <= bins_input[bin_ind]:
            hist[bin_ind - 1] += 1
            x_ind += 1
        else:
            bin_ind += 1

    for i in range(0, 101):
        hist[i] = float(hist[i]) / len(x_input)

    for i in range(1, 101):
        hist[i] = hist[i] + hist[i-1]
    
    return hist


exp_datas = {}

EXPERIMENT_IDS = ['EXPERIMENT_ID_PLACEHOLDER']

for experiment_id in EXPERIMENT_IDS:
    exp_data = get_experiment_data(experiment_id)
    if "exception" in exp_data:
        print("Invalid data is returned: %s" % exp_data["exception"])
    exp_datas[experiment_id] = exp_data

all_samples = {}

for experiment_id, data in exp_datas.items():
    all_samples[experiment_id] = []
    for d in data["meta"]:
        result = d['result']
        if 'sample' in result:
            for sample in result['sample']:
                if 'classification_result' in sample:
                    all_samples[experiment_id].append(sample)
                    
tags = ['All Samples', 'Hard Negative', 'In Junction', 'Into Perpendicular', 'Location: Coit Tower', 'Location: Other', 'Location: SLAC', 'U-Turn']

for tag in tags:
    print('Tag: %s' % tag)
    pr_curve_fig = go.Figure()
    pr_curve_fig.update_layout(
        title='Precision-Recall Curve',
        xaxis_title='Recall',
        yaxis_title='Precision'
    )
    pr_curve_fig.update_layout(
        autosize=False,
        width=800,
        height=600,
    )
    for experiment_id, samples in all_samples.items():
        print('Number of events in experiment {}: {}'.format(experiment_id, \
             len([d for d in exp_datas[experiment_id]['meta'] if tag == 'All Samples' \
                  or tag in d['result']['sample'][0]['tags']])))
        samples_with_tag = []
        for sample in samples:
            if tag ==  'All Samples' or tag in sample['tags']:
                samples_with_tag.append(sample)
        total_samples = len(samples_with_tag)
        pr_points = calculatePRPoints(samples_with_tag)
        print('Number of samples in experiemnt {}: {}'.format(experiment_id, total_samples))
        dtype = [('precision', float), ('recall', float), ('score', float), ('num_results', int)]
        points = np.empty(len(pr_points), dtype=dtype)
        for i, pr_point in enumerate(pr_points):
            points[i] = (pr_point.precision, pr_point.recall, pr_point.score, pr_point.num_results)
            
        np.sort(points, order=['recall'])
        pr_curve_fig = pr_curve_fig.add_trace(go.Scatter(
            name = experiment_id,
            x=points['recall'], 
            y=points['precision']
        ))
    pr_curve_fig.show()
        
    pos_flicker_fig = go.Figure()
    pos_flicker_fig.update_layout(
        title='Positive flicker rate',
        xaxis_title='Flicker fraction',
        yaxis_title='Cumulative histogram'
    )
    pos_flicker_fig.update_layout(
        autosize=False,
        width=800,
        height=600,
    )
    
    neg_flicker_fig = go.Figure()
    neg_flicker_fig.update_layout(
        title='Negative flicker rate',
        xaxis_title='Flicker fraction',
        yaxis_title='Cumulative histogram'
    )
    neg_flicker_fig.update_layout(
        autosize=False,
        width=800,
        height=600,
    )
    
    tpp_fig = go.Figure()
    tpp_fig.update_layout(
        title='Time to predict',
        xaxis_title='Time-to-predict (seconds)',
        yaxis_title='Cumulative histogram'
    )
    tpp_fig.update_layout(
        autosize=False,
        width=800,
        height=600,
    )
    
    for experiment_id, data in exp_datas.items():
        pos_flickers = []
        neg_flickers = []
        time_to_predicts = []
        for d in data['meta']:
            if tag !=  'All Samples' and tag not in d['result']['sample'][0]['tags']:
                continue
            if 'flicker_rate' in d:
                if d['result']['sample'][0]['classification_result']['label']:
                    pos_flickers.append(d['flicker_rate'])
                else:
                    neg_flickers.append(d['flicker_rate'])
            
            if 'time_to_predict' in d:
                if isinstance(d['time_to_predict'], str):
                    time_to_predicts.append(sys.float_info.max)
                elif d['time_to_predict'] >= 0.0:
                    time_to_predicts.append(d['time_to_predict'])

        pos_flickers.sort()
        neg_flickers.sort()
        time_to_predicts.sort()

        bins = []
        ttp_bins = []
        pos_flicker_hist = []
        neg_flicker_hist = []
        tpp_hist = []
        for i in range(-1, 101):
            bins.append(float(i) / 100)
            ttp_bins.append(float(i) / 10)
            if i >= 0:
                pos_flicker_hist.append(0.0)
                neg_flicker_hist.append(0.0)
                tpp_hist.append(0.0)

        pos_flicker_hist = histogram(pos_flicker_hist, pos_flickers, bins)

        dtype = [('flicker_rate', float), ('flicker_fraction', float)]
        points = np.empty(len(pos_flicker_hist), dtype=dtype)
        for i, hist_val in enumerate(pos_flicker_hist):
            points[i] = (pos_flicker_hist[i], bins[i + 1])

        np.sort(points, order=['flicker_fraction'])
        pos_flicker_fig = pos_flicker_fig.add_trace(go.Scatter(
            name = experiment_id,
            x=points['flicker_fraction'], 
            y=points['flicker_rate']
        ))        
        
        neg_flicker_hist = histogram(neg_flicker_hist, neg_flickers, bins)

        dtype = [('flicker_rate', float), ('flicker_fraction', float)]
        points = np.empty(len(neg_flicker_hist), dtype=dtype)
        for i, hist_val in enumerate(neg_flicker_hist):
            points[i] = (neg_flicker_hist[i], bins[i + 1])

        np.sort(points, order=['flicker_fraction'])
        neg_flicker_fig = neg_flicker_fig.add_trace(go.Scatter(
            name = experiment_id,
            x=points['flicker_fraction'], 
            y=points['flicker_rate']
        ))
        
        
        tpp_hist = histogram(tpp_hist, time_to_predicts, ttp_bins)
        dtype = [('time_to_predict', float), ('time_fraction', float)]
        points = np.empty(len(tpp_hist), dtype=dtype)
        for i, hist_val in enumerate(tpp_hist):
            points[i] = (tpp_hist[i], ttp_bins[i + 1])

        np.sort(points, order=['time_fraction'])
        tpp_fig = tpp_fig.add_trace(go.Scatter(
            name = experiment_id,
            x=points['time_fraction'], 
            y=points['time_to_predict']
        ))
        
    pos_flicker_fig.show()
    neg_flicker_fig.show()           
    tpp_fig.show()